In [6]:
!sudo apt update
!sudo apt install libcairo2-dev \
    texlive texlive-latex-extra texlive-fonts-extra \
    texlive-latex-recommended texlive-science \
    tipa libpango1.0-dev
!pip install manim
!pip install IPython==8.21.0

Hit:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:3 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:5 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:7 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
55 packages can be upgraded. Run 'apt list --upgradable' to see them.
W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InR

In [1]:
from manim import *

In [15]:
%%manim -qm -v WARNING SquareToCircle

class SquareToCircle(Scene):
   def construct(self):
      square = Square()
      circle = Circle()
      circle.set_fill(PINK, opacity=0.5)
      self.play(Create(square))
      self.play(Transform(square, circle))
      self.wait()

Manim Community v0.19.0

In [16]:
%%manim -qm -v WARNING BasicAnimation

class BasicAnimation(Scene):
    def construct(self):
        # Create a circle
        circle = Circle()

        # Animate the creation of the circle
        self.play(Create(circle))
        self.wait()

        # Change the circle's color to red
        self.play(circle.animate.set_color(RED))
        self.wait()

        # Transform the circle into a square
        square = Square()
        self.play(Transform(circle, square))
        self.wait()

        # Move the square to the left
        self.play(circle.animate.to_edge(LEFT))
        self.wait()

        # Add text next to the square
        text = Text("Hello Manim!").next_to(circle, RIGHT)
        self.play(Write(text))
        self.wait()

        # Rotate the square
        self.play(circle.animate.rotate(PI/4))
        self.wait()

        # Fade out all elements
        self.play(FadeOut(circle), FadeOut(text))
        self.wait()

Manim Community v0.19.0

In [17]:
%%manim -qm -v WARNING StableEquilibrium

class StableEquilibrium(Scene):
    def construct(self):
        # Title
        title = Text("Stable Equilibrium").scale(0.8)
        self.play(Write(title))
        self.wait(1)
        self.play(title.animate.to_edge(UP))

        # Axes
        axes = Axes(
            x_range=[-3, 3, 1],
            y_range=[-3, 3, 1],
            x_length=6,
            y_length=6,
            axis_config={"include_tip": False, "include_numbers": False},
        ).shift(DOWN * 0.5)
        self.play(Create(axes))

        # Origin
        origin = Dot(axes.c2p(0, 0), color=RED)
        origin_label = MathTex("x=0").next_to(origin, DOWN, buff=0.2).scale(0.7)
        self.play(Create(origin), Write(origin_label))

        # Epsilon circle
        epsilon = ValueTracker(2)
        epsilon_circle = always_redraw(lambda: Circle(
            radius=epsilon.get_value() * axes.x_axis.get_unit_size(),
            color=BLUE,
            stroke_width=2
        ).move_to(origin.get_center()))
        epsilon_label = always_redraw(lambda: MathTex(r"\epsilon").next_to(epsilon_circle, RIGHT, buff=0.1).scale(0.7))
        self.play(Create(epsilon_circle), Write(epsilon_label))

        # Delta circle
        delta = ValueTracker(0.8)
        delta_circle = always_redraw(lambda: Circle(
            radius=delta.get_value() * axes.x_axis.get_unit_size(),
            color=GREEN,
            stroke_width=2
        ).move_to(origin.get_center()))
        delta_label = always_redraw(lambda: MathTex(r"\delta").next_to(delta_circle, LEFT, buff=0.1).scale(0.7))
        self.play(Create(delta_circle), Write(delta_label))

        # t0
        t0 = 0
        t0_label = MathTex(r"t_0").scale(0.7).to_edge(LEFT).shift(UP*1.5)
        self.add(t0_label)

        # Initial condition x(t0)
        x0_dot = Dot(axes.c2p(delta.get_value() * 0.7, delta.get_value() * 0.5), color=YELLOW)
        x0_label = MathTex("x(t_0)").next_to(x0_dot, UP, buff=0.2).scale(0.6)
        self.play(Create(x0_dot), Write(x0_label))

        # Trajectory
        trajectory = VMobject(color=YELLOW, stroke_width=3)
        trajectory.set_points_as_corners([x0_dot.get_center(), x0_dot.get_center()])

        def update_trajectory(mob, dt):
            last_point = mob.get_last_point()
            if np.linalg.norm(last_point - origin.get_center()) < epsilon.get_value() * axes.x_axis.get_unit_size():
                angle = np.arctan2(last_point[1] - origin.get_center()[1], last_point[0] - origin.get_center()[0])
                new_point = last_point + 0.1 * dt * np.array([np.cos(angle + 0.7), np.sin(angle+ 0.7), 0])
                mob.add_points_as_corners([new_point])

        trajectory.add_updater(update_trajectory)
        self.add(trajectory)

        # Explanation
        explanation = VGroup(
            MathTex(r"\text{Stable: If }", r"\|x(t_0)\|", r"<", r"\delta", r"\Rightarrow", r"\|x(t, x_0, t_0)\|<", r"\epsilon", r", \forall t \geq t_0"),
            Text("Trajectory stays inside the epsilon circle").scale(0.6)
        ).arrange(DOWN).to_edge(RIGHT).shift(UP * 1)

        self.play(Write(explanation[0]))


        self.wait(2)
        #Animate delta
        self.play(
                delta.animate.set_value(0.5),
                x0_dot.animate.move_to(axes.c2p(delta.get_value() * 0.8, delta.get_value() * 0.2)),
                x0_label.animate.next_to(x0_dot, UP, buff=0.2),
                run_time=2,
            )

        self.wait(4)
        self.play(Write(explanation[1]))

        self.wait(2)

        #Change epsilon
        self.play(
                epsilon.animate.set_value(1),
                run_time=2,
            )
        self.wait(2)
        self.play(
                delta.animate.set_value(0.3),
                x0_dot.animate.move_to(axes.c2p(delta.get_value() * 0.6, delta.get_value() * 0.5)),
                x0_label.animate.next_to(x0_dot, UP, buff=0.2),
                run_time=2,
            )

        self.wait(5)
        trajectory.clear_updaters()
        self.play(FadeOut(explanation),FadeOut(trajectory),FadeOut(x0_dot),FadeOut(x0_label))
        self.wait()

        # Show dependence on t0
        explanation_t0 = Text("Note: δ depends on ε and t0").scale(0.7).to_edge(RIGHT)
        self.play(Write(explanation_t0))
        self.wait(1)

        # Change t0
        new_t0_label = MathTex(r"t_0'").scale(0.7).next_to(t0_label, RIGHT, buff=0.5)
        self.play(Write(new_t0_label))
        self.wait(1)

        # Reset delta for new t0
        self.play(delta.animate.set_value(0.8))
        self.wait(1)

        # Show that for the same epsilon, delta might need to be smaller for a different t0
        self.play(delta.animate.set_value(0.2))
        self.wait(2)

        self.play(FadeOut(explanation_t0), FadeOut(new_t0_label))
        self.wait(1)

        # Cleanup
        self.play(
            FadeOut(title),
            FadeOut(axes),
            FadeOut(origin),
            FadeOut(origin_label),
            FadeOut(epsilon_circle),
            FadeOut(epsilon_label),
            FadeOut(delta_circle),
            FadeOut(delta_label),
            FadeOut(t0_label)
        )
        self.wait(2)

Manim Community v0.19.0

In [21]:
%%manim -qm -v WARNING AttractiveEquilibrium


class AttractiveEquilibrium(Scene):
    def construct(self):
        # Create coordinate system
        axes = Axes(
            x_range=[-4, 4, 1],
            y_range=[-4, 4, 1],
            x_length=7,
            y_length=7,
            axis_config={"color": BLUE},
        )
        axes_labels = axes.get_axis_labels(x_label="x_1", y_label="x_2")

        # Create region circles
        rho = 3.0
        eta = 0.75
        rho_circle = Circle(radius=rho, color=GREEN, fill_opacity=0.1)
        rho_label = MathTex(r"\rho").next_to(rho_circle, UP)
        eta_circle = Circle(radius=eta, color=RED, fill_opacity=0.2)
        eta_label = MathTex(r"\eta").next_to(eta_circle, UP)

        # Create multiple decaying trajectories
        def create_trajectory(decay_factor):
            return ParametricFunction(
                lambda t: np.array([
                    (rho * 0.8 * np.exp(-decay_factor*t)) * np.cos(3*t),
                    (rho * 0.8 * np.exp(-decay_factor*t)) * np.sin(3*t),
                    0
                ]),
                t_range=[0, 3*PI],
                color=YELLOW,
                stroke_width=3
            )

        trajectories = VGroup(*[create_trajectory(0.4 + 0.1*i) for i in range(3)])
        dots = VGroup(*[Dot(color=YELLOW) for _ in range(3)])
        paths = VGroup(*[TracedPath(dot.get_center, stroke_color=YELLOW, stroke_width=3)
                       for dot in dots])

        # Mathematical definition
        definition = MathTex(
            r"\exists \rho > 0 : \forall \eta > 0, t_0 > 0, \exists T > 0:\\",
            r"\|x(t_0)\| < \rho \implies \|x(t)\| < \eta \quad \forall t \geq t_0 + T"
        ).scale(0.65).to_edge(UP)

        # Lecture information
        lecture_info = Text(
            "Dr. Arnab Maity, AE 666: Adaptive and Learning Control Systems - Lecture 3",
            font_size=20
        ).to_edge(DOWN)

        # Animation sequence
        self.play(Create(axes), Write(axes_labels))
        self.wait()

        # Draw region boundaries
        self.play(
            LaggedStart(
                Create(rho_circle),
                Write(rho_label),
                Create(eta_circle),
                Write(eta_label),
                lag_ratio=0.5
            ),
            run_time=3
        )
        self.wait()

        # Show definition and lecture info
        self.play(Write(definition), Write(lecture_info))
        self.wait(2)

        # Animate multiple trajectories
        self.add(paths, dots)
        for dot, trajectory in zip(dots, trajectories):
            self.play(
                MoveAlongPath(dot, trajectory),
                rate_func=linear,
                run_time=5
            )
        self.wait()

        # Add convergence annotations
        convergence_group = VGroup(
            Text("Convergence time T depends on:", font_size=24),
            Text("- Initial conditions (x₀)", font_size=22),
            Text("- Parameters (ρ, η)", font_size=22)
        ).arrange(DOWN).next_to(axes, RIGHT)

        convergence_arrow = Arrow(
            start=trajectories[0].get_end() + LEFT,
            end=eta_circle.get_center(),
            color=WHITE
        )

        self.play(
            Create(convergence_arrow),
            Write(convergence_group),
            run_time=2
        )
        self.wait(2)

        # Initial condition boundary highlight
        rho_highlight = rho_circle.copy().set_color(GREEN).set_stroke(width=3)
        rho_text = Text("Initial conditions\nmust start within ρ-ball",
                       font_size=22).next_to(rho_circle, LEFT)

        self.play(
            Create(rho_highlight),
            Write(rho_text),
            run_time=2
        )
        self.wait(3)

        # Final convergence demonstration
        final_convergence = Text("All trajectories eventually stay\nwithin η-bound after time T",
                               font_size=24, color=YELLOW).next_to(eta_circle, DOWN)
        self.play(Write(final_convergence))
        self.wait(3)

Manim Community v0.19.0

In [26]:
%%manim -qm -v WARNING AsymptoticStability


class AsymptoticStability(Scene):
    def construct(self):
        # Create coordinate system
        axes = Axes(
            x_range=[-3, 3, 1],
            y_range=[-3, 3, 1],
            x_length=6,
            y_length=6,
            axis_config={"color": BLUE},
        )
        axes_labels = axes.get_axis_labels(x_label="x_1", y_label="x_2")

        # Create stability and attraction regions
        epsilon = 2.0
        delta = 1.0
        rho = 1.5

        epsilon_circle = Circle(radius=epsilon, color=RED, fill_opacity=0.1)
        epsilon_label = MathTex(r"\epsilon").next_to(epsilon_circle, UP)

        delta_circle = Circle(radius=delta, color=GREEN, fill_opacity=0.1)
        delta_label = MathTex(r"\delta(\epsilon)").next_to(delta_circle, LEFT)

        rho_circle = Circle(radius=rho, color=BLUE, fill_opacity=0.1)
        rho_label = MathTex(r"\rho").next_to(rho_circle, DOWN)

        # Create converging trajectory
        trajectory = ParametricFunction(
            lambda t: np.array([
                delta * np.exp(-0.6*t) * np.cos(3*t),
                delta * np.exp(-0.6*t) * np.sin(3*t),
                0
            ]),
            t_range=[0, 3*PI],
            color=YELLOW,
            stroke_width=4
        )

        # Create moving dot and path
        dot = Dot(color=YELLOW).move_to(trajectory.get_start())
        path = TracedPath(dot.get_center, stroke_color=YELLOW, stroke_width=4)

        # Mathematical definitions
        stability_def = MathTex(
            r"\text{Stable: } \forall \epsilon > 0, \exists \delta > 0 :",
            r"\|x(t_0)\| < \delta \implies \|x(t)\| < \epsilon \quad \forall t \geq t_0"
        ).scale(0.6).to_edge(UP)

        attractive_def = MathTex(
            r"\text{Attractive: } \exists \rho > 0 : \forall \eta > 0, \exists T > 0 :",
            r"\|x(t_0)\| < \rho \implies \|x(t)\| < \eta \quad \forall t \geq t_0 + T"
        ).scale(0.6).next_to(stability_def, DOWN, buff=0.2)

        combined_def = Text("Asymptotically Stable = Stable + Attractive",
                          font_size=30, color=YELLOW).to_edge(DOWN)

        # Lecture information
        lecture_info = Text(
            "Dr. Arnab Maity, AE 666: Adaptive and Learning Control Systems - Lecture 3",
            font_size=20
        ).to_edge(DOWN)

        # Animation sequence
        self.play(Create(axes), Write(axes_labels))
        self.wait()

        # Draw stability regions
        self.play(
            LaggedStart(
                Create(epsilon_circle),
                Write(epsilon_label),
                Create(delta_circle),
                Write(delta_label),
                lag_ratio=0.5
            ),
            run_time=3
        )
        self.add(stability_def)
        self.wait(2)

        # Show stability property
        self.add(path, dot)
        self.play(
            MoveAlongPath(dot, trajectory),
            rate_func=linear,
            run_time=5
        )
        self.wait()

        # Transition to attraction property
        self.play(
            FadeOut(stability_def),
            Create(rho_circle),
            Write(rho_label),
            run_time=2
        )
        self.add(attractive_def)
        self.wait(2)

        # Show combined definition
        self.play(
            ReplacementTransform(VGroup(stability_def, attractive_def), combined_def),
            FadeOut(lecture_info)
        )
        self.wait(2)

        # Demonstrate asymptotic stability
        asymptotic_text = VGroup(
            Text("1. Stays within ε-bound (Stability)", font_size=24, color=GREEN),
            Text("2. Converges to origin (Attractiveness)", font_size=24, color=RED)
        ).arrange(DOWN).next_to(axes, RIGHT)

        self.play(Write(asymptotic_text))

        # Animate multiple orbits
        for _ in range(2):
            self.play(
                MoveAlongPath(dot, trajectory),
                rate_func=linear,
                run_time=5
            )
        self.wait(3)

        # Final convergence highlight
        convergence_arrow = Arrow(
            start=trajectory.get_end() + LEFT,
            end=ORIGIN,
            color=WHITE,
            buff=0.1
        )
        convergence_label = Text("Convergence to Equilibrium",
                               font_size=24).next_to(convergence_arrow, DOWN)

        self.play(
            Create(convergence_arrow),
            Write(convergence_label)
        )
        self.wait(3)

Manim Community v0.19.0

In [27]:
%%manim -qm -v WARNING UniformStability

class UniformStability(Scene):
    def construct(self):
        # Coordinate system setup
        axes = Axes(
            x_range=[-3, 3, 1],
            y_range=[-3, 3, 1],
            x_length=6,
            y_length=6,
            axis_config={"color": BLUE},
        )
        axes_labels = axes.get_axis_labels(x_label="x_1", y_label="x_2")

        # Stability boundaries
        epsilon = 2.5
        delta = 1.2
        epsilon_circle = Circle(radius=epsilon, color=RED, fill_opacity=0.1)
        epsilon_label = MathTex(r"\epsilon").next_to(epsilon_circle, UR)
        delta_circle = Circle(radius=delta, color=GREEN, fill_opacity=0.2)
        delta_label = MathTex(r"\delta(\epsilon)").next_to(delta_circle, UL)

        # Multiple phase-shifted trajectories
        def create_orbit(phase):
            return ParametricFunction(
                lambda t: np.array([
                    delta * np.cos(t + phase),
                    delta * np.sin(t + phase),
                    0
                ]),
                t_range=[0, 2*PI],
                color=YELLOW,
                stroke_width=3
            )

        orbits = VGroup(*[create_orbit(i*PI/2) for i in range(4)])
        dots = VGroup(*[Dot(color=YELLOW) for _ in range(4)])
        paths = VGroup(*[TracedPath(dot.get_center, stroke_color=YELLOW, stroke_width=3)
                       for dot in dots])

        # Mathematical definition
        definition = MathTex(
            r"\text{Uniform Stability: } \forall \epsilon > 0, \exists \delta(\epsilon) > 0 :",
            r"\|x(t_0)\| < \delta \implies \|x(t)\| < \epsilon \quad \forall t \geq t_0"
        ).scale(0.65).to_edge(UP)

        # Lecture context
        lecture_info = Text(
            "Dr. Arnab Maity, AE 666: Adaptive and Learning Control Systems - Lecture 3",
            font_size=20
        ).to_edge(DOWN)

        # Animation sequence
        self.play(Create(axes), Write(axes_labels))
        self.wait()

        # Draw stability regions
        self.play(
            LaggedStart(
                Create(epsilon_circle),
                Write(epsilon_label),
                Create(delta_circle),
                Write(delta_label),
                lag_ratio=0.5
            ),
            run_time=3
        )
        self.wait()

        # Show mathematical definition
        self.play(Write(definition), Write(lecture_info))
        self.wait(2)

        # Animate multiple orbits with different initial phases
        self.add(paths, dots)
        for dot, orbit in zip(dots, orbits):
            self.play(
                MoveAlongPath(dot, orbit),
                rate_func=linear,
                run_time=6
            )
        self.wait()

        # Time-independence demonstration
        t0_demo = VGroup(
            Text("Key Property: δ independent of t₀", font_size=26, color=YELLOW),
            Text("Same δ works for all initial times", font_size=24)
        ).arrange(DOWN).next_to(axes, RIGHT)

        phase_arrows = VGroup(*[
            Arrow(
                start=dot.get_center(),
                end=dot.get_center() + 0.5*RIGHT,
                color=WHITE,
                buff=0.1
            ) for dot in dots
        ])

        self.play(
            Write(t0_demo),
            LaggedStart(*[Create(a) for a in phase_arrows]),
            run_time=2
        )
        self.wait(3)

        # Final comparison with regular stability
        comparison = Text("Uniform vs Regular Stability:\nδ(ε) vs δ(ε,t₀)",
                        font_size=26).next_to(axes, LEFT)
        self.play(Write(comparison))
        self.wait(3)

Manim Community v0.19.0

In [28]:
%%manim -qm -v WARNING UniformlyAttractive

class UniformlyAttractive(Scene):
    def construct(self):
        # Coordinate system setup
        axes = Axes(
            x_range=[-4, 4, 1],
            y_range=[-4, 4, 1],
            x_length=7,
            y_length=7,
            axis_config={"color": BLUE},
        )
        axes_labels = axes.get_axis_labels(x_label="x_1", y_label="x_2")

        # Create stability regions
        rho = 3.0
        eta = 0.8
        rho_circle = Circle(radius=rho, color=GREEN, fill_opacity=0.1)
        rho_label = MathTex(r"\rho").next_to(rho_circle, UR)
        eta_circle = Circle(radius=eta, color=RED, fill_opacity=0.2)
        eta_label = MathTex(r"\eta").next_to(eta_circle, UP)

        # Create multiple trajectories with different initial phases but same convergence time
        def create_trajectory(phase):
            return ParametricFunction(
                lambda t: np.array([
                    (rho * 0.9 * np.exp(-0.7*t)) * np.cos(3*t + phase),
                    (rho * 0.9 * np.exp(-0.7*t)) * np.sin(3*t + phase),
                    0
                ]),
                t_range=[0, 3],
                color=YELLOW,
                stroke_width=3
            )

        trajectories = VGroup(*[create_trajectory(i*PI/2) for i in range(4)])
        dots = VGroup(*[Dot(color=YELLOW) for _ in range(4)])
        paths = VGroup(*[TracedPath(dot.get_center, stroke_color=YELLOW, stroke_width=3)
                       for dot in dots])

        # Mathematical definition
        definition = MathTex(
            r"\exists \rho > 0 : \forall \eta > 0, \exists T(\rho,\eta) > 0:",
            r"\|x(t_0)\| < \rho \implies \|x(t)\| < \eta \quad \forall t \geq t_0 + T"
        ).scale(0.65).to_edge(UP)

        # Lecture information
        lecture_info = Text(
            "Dr. Arnab Maity, AE 666: Adaptive and Learning Control Systems - Lecture 3",
            font_size=20
        ).to_edge(DOWN)

        # Time markers and labels
        time_indicator = Line(UP, DOWN).scale(0.5).set_color(WHITE)
        time_label = always_redraw(lambda: Text(f"T = {1.5}", font_size=24)
                                  .next_to(time_indicator, RIGHT))

        # Animation sequence
        self.play(Create(axes), Write(axes_labels))
        self.wait()

        # Draw regions
        self.play(
            LaggedStart(
                Create(rho_circle),
                Write(rho_label),
                Create(eta_circle),
                Write(eta_label),
                lag_ratio=0.5
            ),
            run_time=3
        )
        self.wait()

        # Show definition and lecture info
        self.play(Write(definition), Write(lecture_info))
        self.wait(2)

        # Animate trajectories
        self.add(paths, dots)
        for dot, trajectory in zip(dots, trajectories):
            self.play(
                MoveAlongPath(dot, trajectory),
                rate_func=linear,
                run_time=5
            )
        self.wait()

        # Add time independence demonstration
        time_indicator_group = VGroup(time_indicator, time_label).to_edge(LEFT)
        convergence_text = Text("Uniform Convergence Time\nT(ρ,η) independent of t₀",
                              font_size=24).next_to(time_indicator, RIGHT)

        self.play(
            Create(time_indicator_group),
            Write(convergence_text)
        )
        self.wait(2)

        # Highlight simultaneous convergence
        convergence_arrows = VGroup(*[
            Arrow(
                start=traj.get_end() + 0.5*LEFT,
                end=eta_circle.get_center(),
                color=WHITE
            ) for traj in trajectories
        ])

        self.play(
            LaggedStart(*[Create(a) for a in convergence_arrows]),
            run_time=2
        )
        self.wait(3)

        # Initial condition boundary reminder
        rho_note = Text("Initial conditions must start\nwithin ρ-ball",
                       font_size=22).next_to(rho_circle, LEFT)
        self.play(Write(rho_note))
        self.wait(2)

        # Final comparison
        comparison = Text("Key Difference from Regular Attractiveness:\nT depends only on ρ, η",
                        font_size=24).to_edge(DOWN)
        self.play(ReplacementTransform(lecture_info, comparison))
        self.wait(3)

Manim Community v0.19.0

In [30]:
%%manim -qm -v WARNING UniformAsymptoticStability

class UniformAsymptoticStability(Scene):
    def construct(self):
        # Coordinate system setup
        axes = Axes(
            x_range=[-3.5, 3.5, 1],
            y_range=[-3.5, 3.5, 1],
            x_length=7,
            y_length=7,
            axis_config={"color": BLUE},
        )
        axes_labels = axes.get_axis_labels(x_label="x_1", y_label="x_2")

        # Stability and attraction parameters
        epsilon = 3.0
        delta = 1.5
        rho = 2.5
        eta = 0.6

        # Region circles
        epsilon_circle = Circle(radius=epsilon, color=RED, fill_opacity=0.1)
        epsilon_label = MathTex(r"\epsilon").next_to(epsilon_circle, UR)

        delta_circle = Circle(radius=delta, color=GREEN, fill_opacity=0.2)
        delta_label = MathTex(r"\delta(\epsilon)").next_to(delta_circle, UL)

        eta_circle = Circle(radius=eta, color=ORANGE, fill_opacity=0.3)
        eta_label = MathTex(r"\eta").next_to(eta_circle, UP)

        # Converging trajectories with different initial phases
        def create_trajectory(phase):
            return ParametricFunction(
                lambda t: np.array([
                    (delta * np.exp(-0.8*t)) * np.cos(3*t + phase),
                    (delta * np.exp(-0.8*t)) * np.sin(3*t + phase),
                    0
                ]),
                t_range=[0, 4],
                color=YELLOW,
                stroke_width=3
            )

        trajectories = VGroup(*[create_trajectory(i*PI/2) for i in range(4)])
        dots = VGroup(*[Dot(color=YELLOW) for _ in range(4)])
        paths = VGroup(*[TracedPath(dot.get_center, stroke_color=YELLOW, stroke_width=3)
                       for dot in dots])

        # Mathematical definitions
        stability_def = MathTex(
            r"\text{Uniform Stability: } \forall \epsilon > 0, \exists \delta(\epsilon) > 0 :",
            r"\|x(t_0)\| < \delta \implies \|x(t)\| < \epsilon \quad \forall t \geq t_0"
        ).scale(0.6).to_edge(UP)

        attractive_def = MathTex(
            r"\text{Uniform Attractiveness: } \exists T(\rho,\eta) > 0 :",
            r"\|x(t_0)\| < \rho \implies \|x(t)\| < \eta \quad \forall t \geq t_0 + T"
        ).scale(0.6).next_to(stability_def, DOWN, buff=0.2)

        combined_def = Text("Uniform Asymptotic Stability = \nUniform Stability + Uniform Attractiveness",
                          font_size=30, color=YELLOW).to_edge(DOWN)

        # Lecture information
        lecture_info = Text(
            "Dr. Arnab Maity, AE 666: Adaptive and Learning Control Systems - Lecture 3",
            font_size=20
        ).to_edge(DOWN)

        # Time indicator system
        timeline = NumberLine(
            x_range=[0, 5],
            length=5,
            color=WHITE,
            include_numbers=True
        ).to_edge(DOWN).shift(UP*0.5)
        time_label = Text("Convergence Time T(ρ,η)", font_size=24).next_to(timeline, DOWN)

        # Animation sequence
        self.play(Create(axes), Write(axes_labels))
        self.wait()

        # Draw stability regions
        self.play(
            LaggedStart(
                Create(epsilon_circle),
                Write(epsilon_label),
                Create(delta_circle),
                Write(delta_label),
                Create(eta_circle),
                Write(eta_label),
                lag_ratio=0.4
            ),
            run_time=4
        )
        self.wait()

        # Show mathematical definitions
        self.play(Write(stability_def), Write(lecture_info))
        self.wait(2)

        # Animate stability property
        self.add(paths, dots)
        for dot, trajectory in zip(dots, trajectories):
            self.play(
                MoveAlongPath(dot, trajectory),
                rate_func=linear,
                run_time=3
            )
        self.wait()

        # Transition to attractiveness
        self.play(
            ReplacementTransform(stability_def, attractive_def),
            FadeOut(lecture_info),
            Create(timeline),
            Write(time_label)
        )
        self.wait(2)

        # Highlight uniform convergence
        convergence_markers = VGroup(*[
            Dot(color=WHITE).move_to(traj.get_end())
            for traj in trajectories
        ])
        convergence_lines = VGroup(*[
            DashedLine(marker.get_center(), eta_circle.get_center(), color=WHITE)
            for marker in convergence_markers
        ])

        self.play(
            LaggedStart(*[Create(m) for m in convergence_markers]),
            LaggedStart(*[Create(l) for l in convergence_lines]),
            run_time=2
        )
        self.wait()

        # Show combined property
        self.play(
            ReplacementTransform(VGroup(attractive_def, stability_def), combined_def),
            FadeOut(VGroup(timeline, time_label, convergence_markers, convergence_lines))
        )
        self.wait(2)

        # Final demonstration
        uniform_text = VGroup(
            Text("1. δ independent of t₀", font_size=24, color=GREEN),
            Text("2. T independent of t₀", font_size=24, color=ORANGE)
        ).arrange(DOWN).next_to(axes, RIGHT)

        self.play(Write(uniform_text))
        self.wait(3)

        # System behavior summary
        summary = Text("All trajectories:\n- Stay within ε-bound\n- Converge uniformly to origin",
                     font_size=28).to_edge(DOWN)
        self.play(Write(summary))
        self.wait(3)

Manim Community v0.19.0

In [33]:

%%manim -qm -v WARNING LocalGlobalAttractiveness

class LocalGlobalAttractiveness(Scene):
    def construct(self):
        # Setup dual coordinate systems with corrected parameters
        left_axes = Axes(
            x_range=[-4,4,1],
            y_range=[-4,4,1],
            x_length=5,  # Changed from width
            y_length=5   # Changed from height
        ).shift(LEFT*3)

        right_axes = Axes(
            x_range=[-6,6,1],
            y_range=[-6,6,1],
            x_length=5,  # Changed from width
            y_length=5   # Changed from height
        ).shift(RIGHT*3)

        # Rest of the code remains the same
        # Titles
        local_title = Text("Local Attractiveness", color=BLUE).scale(0.8).next_to(left_axes, UP)
        global_title = Text("Global Attractiveness", color=GREEN).scale(0.8).next_to(right_axes, UP)

        # Local attractiveness elements
        local_rho = 2.5
        local_rho_circ = Circle(radius=local_rho, color=BLUE_B, fill_opacity=0.1).move_to(left_axes)
        local_rho_label = MathTex(r"\rho_{\text{local}}").next_to(local_rho_circ, UP)

        # Global attractiveness elements
        global_rho_circ = Circle(radius=5, color=GREEN_B, fill_opacity=0.1).move_to(right_axes)
        global_rho_label = MathTex(r"\rho\to\infty").next_to(global_rho_circ, UP)

        # Trajectories
        def local_trajectory(start_angle):
            return ParametricFunction(
                lambda t: np.array([
                    (local_rho*0.8 * np.exp(-0.6*t)) * np.cos(3*t + start_angle),
                    (local_rho*0.8 * np.exp(-0.6*t)) * np.sin(3*t + start_angle),
                    0
                ]), t_range=[0, 3], color=YELLOW
            ).move_to(left_axes)

        def global_trajectory(start_radius):
            return ParametricFunction(
                lambda t: np.array([
                    (start_radius * np.exp(-0.8*t)) * np.cos(3*t),
                    (start_radius * np.exp(-0.8*t)) * np.sin(3*t),
                    0
                ]), t_range=[0, 4], color=YELLOW
            ).move_to(right_axes)

        # Local trajectories
        converging_traj = local_trajectory(0)
        diverging_traj = ParametricFunction(
            lambda t: np.array([3 + t, 3 + t, 0]),
            t_range=[0, 2], color=RED
        ).move_to(left_axes)

        # Global trajectories
        global_traj1 = global_trajectory(4)
        global_traj2 = global_trajectory(5)

        # Text explanations
        local_text = VGroup(
            Text("Local:", color=BLUE),
            Text("- Requires initial condition", font_size=24),
            Text("  within ρ-ball", font_size=24),
            Text("- No guarantee outside ρ", font_size=24, color=RED)
        ).arrange(DOWN).to_edge(LEFT).shift(RIGHT*0.5)

        global_text = VGroup(
            Text("Global:", color=GREEN),
            Text("- Works for any initial", font_size=24),
            Text("  condition (∀ρ > 0)", font_size=24),
            Text("- Uniform convergence", font_size=24)
        ).arrange(DOWN).to_edge(RIGHT).shift(LEFT*0.5)

        # Animation sequence
        self.play(
            Create(left_axes),
            Create(right_axes),
            Write(local_title),
            Write(global_title)
        )
        self.wait()

        # Draw local elements
        self.play(
            Create(local_rho_circ),
            Write(local_rho_label),
            Create(global_rho_circ),
            Write(global_rho_label)
        )
        self.wait()

        # Animate local trajectories
        self.play(Create(converging_traj), run_time=3)
        self.play(Create(diverging_traj), run_time=2)
        self.play(Write(local_text))
        self.wait()

        # Animate global trajectories
        self.play(
            Create(global_traj1),
            Create(global_traj2),
            run_time=5
        )
        self.play(Write(global_text))
        self.wait(3)

        # Final comparison
        comparison = VGroup(
            Text("Key Comparison:", color=YELLOW),
            Text("Local: Finite basin of attraction", color=BLUE),
            Text("Global: Entire state space", color=GREEN)
        ).arrange(DOWN).to_edge(DOWN)

        self.play(
            FadeOut(local_text),
            FadeOut(global_text),
            FadeIn(comparison)
        )
        self.wait(3)

Manim Community v0.19.0

In [34]:
%%manim -qm -v WARNING ExponentialStability

class ExponentialStability(Scene):
    def construct(self):
        # Create coordinate system
        axes = Axes(
            x_range=[0, 5, 1],
            y_range=[0, 3, 0.5],
            x_length=7,
            y_length=4,
            axis_config={"color": BLUE},
            x_axis_config={"numbers_to_include": np.arange(0, 6, 1)},
            y_axis_config={"numbers_to_include": np.arange(0, 3.5, 0.5)}
        ).shift(DOWN*0.5)

        # Stability parameters
        alpha1 = 1.5
        alpha2 = 0.8
        x0 = 2.0  # Initial condition

        # Create exponential bound curve
        bound_curve = axes.plot(
            lambda t: alpha1 * x0 * np.exp(-alpha2 * t),
            x_range=[0, 5],
            color=RED
        )
        bound_label = MathTex(
            r"\alpha_1 \|x_0\| e^{-\alpha_2 t}",
            color=RED
        ).next_to(bound_curve.point_from_proportion(0.6), UR)

        # Create state trajectory
        trajectory = axes.plot(
            lambda t: alpha1 * x0 * np.exp(-alpha2 * t) * (1 + 0.3 * np.sin(3*t)),
            x_range=[0, 5],
            color=YELLOW
        )

        # Create neighborhood circle
        neighborhood = Circle(radius=0.8, color=GREEN, fill_opacity=0.1)
        neighborhood.move_to(axes.c2p(0, 0))
        neighborhood_label = MathTex(r"B_\delta(0)").next_to(neighborhood, UL)

        # Mathematical definition
        definition = MathTex(
            r"\forall t \geq t_0: \quad \|x(t)\| \leq \alpha_1 \|x_0\| e^{-\alpha_2 (t-t_0)}",
            substrings_to_isolate=[r"\alpha_1", r"\alpha_2"]
        ).scale(0.8).to_edge(UP)
        definition.set_color_by_tex(r"\alpha_1", YELLOW)
        definition.set_color_by_tex(r"\alpha_2", ORANGE)

        # Parameter annotations
        alpha_box = VGroup(
            MathTex(r"\alpha_1 = 1.5", color=YELLOW),
            MathTex(r"\alpha_2 = 0.8", color=ORANGE)
        ).arrange(DOWN, aligned_edge=LEFT).to_edge(RIGHT)

        # Animation sequence
        self.play(Create(axes))
        self.play(Write(definition))
        self.wait()

        # Draw neighborhood
        self.play(
            Create(neighborhood),
            Write(neighborhood_label)
        )
        self.wait()

        # Show parameters
        self.play(Write(alpha_box))
        self.wait()

        # Animate bound curve
        self.play(
            Create(bound_curve),
            Write(bound_label),
            run_time=2
        )
        self.wait()

        # Animate actual trajectory
        self.play(
            Create(trajectory),
            run_time=3
        )
        self.wait()

        # Demonstrate multiple trajectories
        def create_decaying_trajectory(alpha1, alpha2, x0, color):
            return axes.plot(
                lambda t: alpha1 * x0 * np.exp(-alpha2 * t) * (1 + 0.3 * np.sin(3*t)),
                x_range=[0, 5],
                color=color
            )

        trajectories = VGroup(
            create_decaying_trajectory(1.2, 1.0, 1.8, BLUE),
            create_decaying_trajectory(1.5, 0.8, 2.0, YELLOW),
            create_decaying_trajectory(2.0, 0.5, 2.2, PINK)
        )

        self.play(
            LaggedStart(*[Create(traj) for traj in trajectories]),
            run_time=4
        )
        self.wait(2)

        # Final comparison
        comparison = VGroup(
            Text("Key Features:", color=YELLOW),
            Text("- Exponential decay rate", font_size=24),
            Text("- Uniform convergence bound", font_size=24),
            Text("- Stability independent of t₀", font_size=24)
        ).arrange(DOWN).to_edge(DOWN)

        self.play(Write(comparison))
        self.wait(3)

Manim Community v0.19.0

In [36]:
%%manim -qm -v WARNING LyapunovStability

class LyapunovStability(Scene):
    def construct(self):
        # Title and introduction
        title = Text("Lyapunov Stability Methods", font_size=40).to_edge(UP)
        self.play(Write(title))
        self.wait(2)

        # Create coordinate system for phase portrait
        axes = Axes(
            x_range=[-3, 3, 1],
            y_range=[-3, 3, 1],
            x_length=6,
            y_length=6
        ).shift(DOWN*0.5)

        # Nonlinear system example
        sys_eq = MathTex(
            r"\dot{x} = f(x,t)",
            font_size=35
        ).to_edge(UP).shift(DOWN*0.5)

        # Lyapunov function visualization (2D energy contour)
        energy_eq = MathTex(
            r"V(x) = x_1^2 + x_2^2",  # Simplified 2D energy function
            font_size=35
        ).next_to(axes, UP)

        # Animate system equations
        self.play(Create(axes), Write(sys_eq))
        self.wait()

        # Show energy function
        self.play(Transform(sys_eq, energy_eq))
        self.wait(2)

        # Energy contour visualization (2D)
        energy_contour = axes.plot_parametric_curve(
            lambda t: np.array([
                np.cos(t),
                np.sin(t),
                0
            ]),
            color=BLUE,
            t_range=[0, 2*PI]
        )

        energy_cond = MathTex(
            r"\dot{V}(x) = \nabla V \cdot f(x) \leq 0",
            font_size=35
        ).next_to(axes, DOWN)

        self.play(
            Create(energy_contour),
            Write(energy_cond)
        )
        self.wait(2)

        # Rest of the code remains the same (2D elements only)
        # ... [keep all other 2D elements unchanged] ...

        # Final comparison table
        final_comp = Table(
            [["Global Analysis", "Local Analysis"],
             ["No Linearization", "Requires Linearization"],
             ["Energy Functions", "Eigenvalues"]],
            col_labels=[Text("Direct Method"), Text("Indirect Method")]
        ).scale(0.7)

        self.play(
            FadeOut(*self.mobjects),
            FadeIn(final_comp)
        )
        self.wait(3)

Manim Community v0.19.0

In [ ]:
%%manim -qm -v WARNING PendulumEnergyAnalysis
import numpy as np

class PendulumEnergyAnalysis(Scene):
    def construct(self):
        # System parameters
        l = 2  # pendulum length
        g = 9.8
        k = 0.5
        m = 1
        initial_angle = PI/2

        # Create pendulum components
        pivot = Dot(point=ORIGIN + UP*0.5, color=WHITE)
        rod = Line(pivot.get_center(), pivot.get_center() + DOWN*l, color=WHITE)
        bob = Dot(point=rod.get_end(), color=BLUE, radius=0.2)
        pendulum = VGroup(pivot, rod, bob)

        # State variables
        x1 = ValueTracker(initial_angle)
        x2 = ValueTracker(0)

        # Energy display
        energy_eq = MathTex(
            r"E = \frac{g}{l}(1 - \cos x_1) + \frac{1}{2}x_2^2",
            font_size=30
        ).to_edge(UP)

        energy_dot_eq = MathTex(
            r"\dot{E} = -\frac{k}{m}x_2^2 \leq 0",
            color=RED,
            font_size=30
        ).next_to(energy_eq, DOWN)

        # Create energy plot axes
        energy_axes = Axes(
            x_range=[0, 10, 1],
            y_range=[0, 5, 1],
            x_length=5,
            y_length=3,
            axis_config={"color": WHITE}
        ).to_edge(RIGHT)
        energy_label = energy_axes.get_y_axis_label("Energy E", direction=UL)

        # Animation setup
        self.play(Create(pendulum), Write(energy_eq))
        self.wait()

        # Add energy plot
        self.play(Create(energy_axes), Write(energy_label))
        energy_dot = Dot(color=YELLOW)
        energy_line = VMobject(color=YELLOW)
        energy_line.start_new_path(energy_axes.c2p(0, 0))

        # Update functions
        def update_pendulum(mob):
            angle = x1.get_value()
            new_end = pivot.get_center() + l * np.sin(angle)*RIGHT + l * (-np.cos(angle))*DOWN
            new_rod = Line(pivot.get_center(), new_end, color=WHITE)
            new_bob = Dot(point=new_end, color=BLUE, radius=0.2)
            mob.become(VGroup(pivot, new_rod, new_bob))

        def update_energy(mob):
            current_energy = (g/l)*(1 - np.cos(x1.get_value())) + 0.5*x2.get_value()**2
            mob.move_to(energy_axes.c2p(self.time, current_energy))
            energy_line.add_line_to(mob.get_center())

        pendulum.add_updater(update_pendulum)
        energy_dot.add_updater(update_energy)

        # Simulation loop
        dt = 0.016  # time step
        x1_val = initial_angle
        x2_val = 0

        for _ in range(250):
            x1_val += x2_val * dt
            x2_val += (-(g/l)*np.sin(x1_val) - (k/m)*x2_val) * dt
            x1.set_value(x1_val)
            x2.set_value(x2_val)
            self.add(energy_line)
            self.wait(dt)

        # Show energy derivative equation
        self.play(Write(energy_dot_eq))
        self.wait(2)

        # Highlight dissipation
        dissipation_box = SurroundingRectangle(energy_dot_eq, color=RED)
        self.play(Create(dissipation_box))
        self.wait(2)

        # Cleanup
        pendulum.clear_updaters()
        energy_dot.clear_updaters()
        self.play(*[FadeOut(mob) for mob in self.mobjects])